In [2]:
import requests
from pprint import pprint
import pandas as pd
import sweetviz 
from pymongo import MongoClient
import json
pd.options.display.max_colwidth = 200

In [4]:
#read in new cleaned csv
cleaned_data= pd.read_csv('../resources/cleaned_animals.csv')
cleaned_data.head()

Unnamed: 0        id organization_id                 name type    age  \
0           0  70490327          TX2305                Davon  Dog  Adult   
1           1  70490328           MO486                 Mack  Dog  Adult   
2           2  70490326           MI812  Lahni! DNA tested!   Dog  Adult   
3           3  70490283           MS214        Jughead Jones  Dog   Baby   
4           4  70490324            AZ57                 Mona  Dog  Young   

   gender         size  \
0    Male        Large   
1  Female  Extra Large   
2  Female        Large   
3    Male        Large   
4  Female        Large   

                                                                                                                                                                                         contact  \
0                {'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}   
1             {'email': 'wonderweimsrescue@gmail.com', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'St. Louis', 'state': 'MO', 'postcode': '63129', 'country': 'US'}}   
2     {'email': 'misfitangels@gmail.com', 'phone': '(586) 339-5443', 'address': {'address1': None, 'address2': None, 'city': 'Eastpointe', 'state': 'MI', 'postcode': '48021', 'country': 'US'}}   
3        {'email': 'myjerichorfb@gmail.com', 'phone': '(662) 401-5799', 'address': {'address1': None, 'address2': None, 'city': 'Baldwyn', 'state': 'MS', 'postcode': '38824', 'country': 'US'}}   
4  {'email': 'blackhathumane@gmail.com', 'phone': '(575) 999-6236', 'address': {'address1': None, 'address2': None, 'city': 'Albuquerque', 'state': 'NM', 'postcode': '87107', 'country': 'US'}}   

                                                                                                                                                                                                       url  
0  https://www.petfinder.com/dog/davon-70490327/or/woodburn/throw-a-dog-a-bone-dog-rescue-tx2305/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7c...  
1  https://www.petfinder.com/dog/mack-70490328/mo/st-louis/wonder-weims-rescue-mo486/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7ce2fffe-d69d-...  
2  https://www.petfinder.com/dog/lahni-dna-tested-70490326/mi/eastpointe/misfit-angels-dog-rescue-mi812/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_con...  
3  https://www.petfinder.com/dog/jughead-jones-70490283/ms/baldwyn/jericho-rescued-fur-babies-ms214/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content...  
4  https://www.petfinder.com/dog/mona-70490324/nm/albuquerque/blackhat-humane-society-az57/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7ce2fffe...

In [5]:
#count unique ids in organization id column 
organization_id= cleaned_data['organization_id'].value_counts()
id_df= pd.DataFrame(organization_id)
id_df

count
organization_id       
AZ101               61
TX46                40
IA260               25
TX236               21
IN113               20
...                ...
WA175                1
IN301                1
MI985                1
MA393                1
KS283                1

[642 rows x 1 columns]

In [6]:
#save organization ids as csv to just review how many id organizations per state have what amount of pets available
id_df.to_csv('sally_organization_id.csv')

In [7]:
#checking how many rows there are initially to reference when i drop duplicates and na 
cleaned_data.count()

Unnamed: 0         2272
id                 2272
organization_id    2272
name               2272
type               2272
age                2272
gender             2272
size               2272
contact            2272
url                2272
dtype: int64

In [8]:
#dropped duplicates, but the amount of rows is the same 2272
drop_dup= cleaned_data.drop_duplicates()
drop_dup.count()


Unnamed: 0         2272
id                 2272
organization_id    2272
name               2272
type               2272
age                2272
gender             2272
size               2272
contact            2272
url                2272
dtype: int64

In [9]:
#dropped na, but amount of rows is the same 2272
drop_na = cleaned_data.dropna()
drop_na.count()

Unnamed: 0         2272
id                 2272
organization_id    2272
name               2272
type               2272
age                2272
gender             2272
size               2272
contact            2272
url                2272
dtype: int64

In [10]:
#after researching more, we decided to drop duplicate pet names that indicate fostered pets, check length of duplicate names to ensure duplicate names get dropped
len(cleaned_data['name'].unique())

1914

In [11]:
#dropping duplicate names from 'name' column
dropped_dup_df= cleaned_data.drop_duplicates(subset=['name'])

#confirming length is the same as the unique names above to ensure duplicate names got dropped
len(dropped_dup_df['name'])

1914

In [12]:
#checking first 20 entries and comparing to old csv to ensure duplicates were removed 
dropped_dup_df.head(20)

Unnamed: 0        id organization_id                 name type    age  \
0            0  70490327          TX2305                Davon  Dog  Adult   
1            1  70490328           MO486                 Mack  Dog  Adult   
2            2  70490326           MI812  Lahni! DNA tested!   Dog  Adult   
3            3  70490283           MS214        Jughead Jones  Dog   Baby   
4            4  70490324            AZ57                 Mona  Dog  Young   
6            6  70490322            WA02               Lilith  Cat  Young   
7            7  70490321           NC516                 Toby  Dog  Adult   
8            8  70490319          CA1750      Angelica Litter  Dog   Baby   
9            9  70490318           TN147                  Dot  Cat  Young   
10          10  70490315          CA2373              Diamond  Dog  Young   
11          11  70490316          TX2584                Ollie  Dog   Baby   
12          12  70490314           CT142            Marshall   Dog  Young   
13          13  70490313          CA2686                Bobbi  Dog   Baby   
16          16  70490309            GA50               SHILOH  Dog  Adult   
18          18  70490305            QC41       Lolo et Ludwig  Cat   Baby   
19          19  70490301          CA2686                Dolly  Dog   Baby   
20          20  70490300           TN147                Yoshi  Cat  Young   
22          22  70490295            WA02                 Leia  Cat  Adult   
23          23  70490293           WA727                Lucky  Dog  Young   
25          25  70490287           TN147           Miss Kitty  Cat  Adult   

    gender         size  \
0     Male        Large   
1   Female  Extra Large   
2   Female        Large   
3     Male        Large   
4   Female        Large   
6   Female       Medium   
7     Male        Large   
8     Male        Small   
9   Female       Medium   
10  Female        Small   
11    Male        Large   
12    Male        Large   
13  Female        Large   
16    Male  Extra Large   
18    Male       Medium   
19  Female        Large   
20    Male       Medium   
22  Female       Medium   
23    Male        Large   
25  Female       Medium   

                                                                                                                                                                                                    contact  \
0                           {'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}   
1                        {'email': 'wonderweimsrescue@gmail.com', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'St. Louis', 'state': 'MO', 'postcode': '63129', 'country': 'US'}}   
2                {'email': 'misfitangels@gmail.com', 'phone': '(586) 339-5443', 'address': {'address1': None, 'address2': None, 'city': 'Eastpointe', 'state': 'MI', 'postcode': '48021', 'country': 'US'}}   
3                   {'email': 'myjerichorfb@gmail.com', 'phone': '(662) 401-5799', 'address': {'address1': None, 'address2': None, 'city': 'Baldwyn', 'state': 'MS', 'postcode': '38824', 'country': 'US'}}   
4             {'email': 'blackhathumane@gmail.com', 'phone': '(575) 999-6236', 'address': {'address1': None, 'address2': None, 'city': 'Albuquerque', 'state': 'NM', 'postcode': '87107', 'country': 'US'}}   
6                            {'email': 'catsadopt@popptricities.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Pasco', 'state': 'WA', 'postcode': '99301', 'country': 'US'}}   
7                      {'email': 'adopt@carolinapaws.com', 'phone': None, 'address': {'address1': 'P.O. Box 365', 'address2': None, 'city': 'Waxhaw', 'state': 'NC', 'postcode': '28173', 'country': 'US'}}   
8   {'email': 'application@lovejoyfoundation.org', 'phone': '(310) 719-5707', 'address': {'address1': '1121 West Hillcrest Blvd.', 'address2': None, 'city': 'Ingl

In [13]:
new_columns = dropped_dup_df['contact'].str.split(',',n=4,expand=True)
address_to_list = new_columns[4].values.tolist()
trying_new_col = [col.split(",") for col in address_to_list]
test_df= pd.DataFrame(trying_new_col)
test_df.head(5)

0               1                     2  \
0      'city': 'Woodburn'   'state': 'OR'   'postcode': '97071'   
1     'city': 'St. Louis'   'state': 'MO'   'postcode': '63129'   
2    'city': 'Eastpointe'   'state': 'MI'   'postcode': '48021'   
3       'city': 'Baldwyn'   'state': 'MS'   'postcode': '38824'   
4   'city': 'Albuquerque'   'state': 'NM'   'postcode': '87107'   

                    3     4  
0   'country': 'US'}}  None  
1   'country': 'US'}}  None  
2   'country': 'US'}}  None  
3   'country': 'US'}}  None  
4   'country': 'US'}}  None

In [14]:
len(test_df)

1914

In [15]:
#renaming headers 
changed_col_name_df= test_df.rename(columns={0:'city',1:'state',2:'zip',3:'cntry',4:'none'})
changed_col_name_df.head()

city           state                   zip  \
0      'city': 'Woodburn'   'state': 'OR'   'postcode': '97071'   
1     'city': 'St. Louis'   'state': 'MO'   'postcode': '63129'   
2    'city': 'Eastpointe'   'state': 'MI'   'postcode': '48021'   
3       'city': 'Baldwyn'   'state': 'MS'   'postcode': '38824'   
4   'city': 'Albuquerque'   'state': 'NM'   'postcode': '87107'   

                cntry  none  
0   'country': 'US'}}  None  
1   'country': 'US'}}  None  
2   'country': 'US'}}  None  
3   'country': 'US'}}  None  
4   'country': 'US'}}  None

In [16]:
#pulling in just city and state columns 
city_state_df= changed_col_name_df[['city','state']]
city_state_df

city           state
0         'city': 'Woodburn'   'state': 'OR'
1        'city': 'St. Louis'   'state': 'MO'
2       'city': 'Eastpointe'   'state': 'MI'
3          'city': 'Baldwyn'   'state': 'MS'
4      'city': 'Albuquerque'   'state': 'NM'
...                      ...             ...
1909      'city': 'Milpitas'   'state': 'CA'
1910      'city': 'Milpitas'   'state': 'CA'
1911      'city': 'Hartwell'   'state': 'GA'
1912      'city': 'Portland'   'state': 'OR'
1913       'city': 'Wichita'   'state': 'KS'

[1914 rows x 2 columns]

In [ ]:
### Start of Kyle's Code ###

In [17]:
city_state_df['city_only'] = city_state_df['city'].str.split(':', expand=True)[1]
city_state_df['city_only'].head()

C:\Users\David Rios\AppData\Local\Temp\ipykernel_45400\3890307498.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  city_state_df['city_only'] = city_state_df['city'].str.split(':', expand=True)[1]


0        'Woodburn'
1       'St. Louis'
2      'Eastpointe'
3         'Baldwyn'
4     'Albuquerque'
Name: city_only, dtype: object

In [16]:
city_state_df['state_only'] = city_state_df['state'].str.split(':', expand=True)[1]
city_state_df['state_only'].head()

/var/folders/92/3rr1k66j0p17gyjv6qwfhzr40000gn/T/ipykernel_87625/4183624009.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  city_state_df['state_only'] = city_state_df['state'].str.split(':', expand=True)[1]


0     'OR'
1     'MO'
2     'MI'
3     'MS'
4     'NM'
Name: state_only, dtype: object

In [17]:
city_state_df

city           state       city_only state_only
0         'city': 'Woodburn'   'state': 'OR'      'Woodburn'       'OR'
1        'city': 'St. Louis'   'state': 'MO'     'St. Louis'       'MO'
2       'city': 'Eastpointe'   'state': 'MI'    'Eastpointe'       'MI'
3          'city': 'Baldwyn'   'state': 'MS'       'Baldwyn'       'MS'
4      'city': 'Albuquerque'   'state': 'NM'   'Albuquerque'       'NM'
...                      ...             ...             ...        ...
1909      'city': 'Milpitas'   'state': 'CA'      'Milpitas'       'CA'
1910      'city': 'Milpitas'   'state': 'CA'      'Milpitas'       'CA'
1911      'city': 'Hartwell'   'state': 'GA'      'Hartwell'       'GA'
1912      'city': 'Portland'   'state': 'OR'      'Portland'       'OR'
1913       'city': 'Wichita'   'state': 'KS'       'Wichita'       'KS'

[1914 rows x 4 columns]

In [18]:
city_state_only_df = city_state_df[['city_only','state_only']]
city_state_only_df

city_only state_only
0         'Woodburn'       'OR'
1        'St. Louis'       'MO'
2       'Eastpointe'       'MI'
3          'Baldwyn'       'MS'
4      'Albuquerque'       'NM'
...              ...        ...
1909      'Milpitas'       'CA'
1910      'Milpitas'       'CA'
1911      'Hartwell'       'GA'
1912      'Portland'       'OR'
1913       'Wichita'       'KS'

[1914 rows x 2 columns]

In [19]:
final_city_state_df= city_state_only_df.rename(columns={'city_only':'city','state_only':'state'})
final_city_state_df.head()

city  state
0      'Woodburn'   'OR'
1     'St. Louis'   'MO'
2    'Eastpointe'   'MI'
3       'Baldwyn'   'MS'
4   'Albuquerque'   'NM'

In [20]:
final_city_state_df

city  state
0         'Woodburn'   'OR'
1        'St. Louis'   'MO'
2       'Eastpointe'   'MI'
3          'Baldwyn'   'MS'
4      'Albuquerque'   'NM'
...              ...    ...
1909      'Milpitas'   'CA'
1910      'Milpitas'   'CA'
1911      'Hartwell'   'GA'
1912      'Portland'   'OR'
1913       'Wichita'   'KS'

[1914 rows x 2 columns]

In [21]:
#pulling in just city and state columns 
city_only_df= final_city_state_df[['city']]
city_only_df

city
0         'Woodburn'
1        'St. Louis'
2       'Eastpointe'
3          'Baldwyn'
4      'Albuquerque'
...              ...
1909      'Milpitas'
1910      'Milpitas'
1911      'Hartwell'
1912      'Portland'
1913       'Wichita'

[1914 rows x 1 columns]

In [22]:
city_only_df['city'] = city_only_df['city'].str.replace("'", "")

print(city_only_df)

              city
0         Woodburn
1        St. Louis
2       Eastpointe
3          Baldwyn
4      Albuquerque
...            ...
1909      Milpitas
1910      Milpitas
1911      Hartwell
1912      Portland
1913       Wichita

[1914 rows x 1 columns]


/var/folders/92/3rr1k66j0p17gyjv6qwfhzr40000gn/T/ipykernel_87625/1316230158.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  city_only_df['city'] = city_only_df['city'].str.replace("'", "")


In [23]:
#pulling in just city and state columns 
state_only_df= final_city_state_df[['state']]
state_only_df

state
0      'OR'
1      'MO'
2      'MI'
3      'MS'
4      'NM'
...     ...
1909   'CA'
1910   'CA'
1911   'GA'
1912   'OR'
1913   'KS'

[1914 rows x 1 columns]

In [24]:
state_only_df['state'] = state_only_df['state'].str.replace("'", "")

print(state_only_df)

     state
0       OR
1       MO
2       MI
3       MS
4       NM
...    ...
1909    CA
1910    CA
1911    GA
1912    OR
1913    KS

[1914 rows x 1 columns]


/var/folders/92/3rr1k66j0p17gyjv6qwfhzr40000gn/T/ipykernel_87625/2335674871.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  state_only_df['state'] = state_only_df['state'].str.replace("'", "")


In [25]:
final_city_state_df= pd.concat([city_only_df, state_only_df], axis=1)

print(final_city_state_df)

              city state
0         Woodburn    OR
1        St. Louis    MO
2       Eastpointe    MI
3          Baldwyn    MS
4      Albuquerque    NM
...            ...   ...
1909      Milpitas    CA
1910      Milpitas    CA
1911      Hartwell    GA
1912      Portland    OR
1913       Wichita    KS

[1914 rows x 2 columns]


In [26]:
#pulling in just city and state columns 
zip_cntry_df= changed_col_name_df[['zip','cntry']]
zip_cntry_df

zip               cntry
0      'postcode': '97071'   'country': 'US'}}
1      'postcode': '63129'   'country': 'US'}}
2      'postcode': '48021'   'country': 'US'}}
3      'postcode': '38824'   'country': 'US'}}
4      'postcode': '87107'   'country': 'US'}}
...                    ...                 ...
1909   'postcode': '95035'   'country': 'US'}}
1910   'postcode': '95035'   'country': 'US'}}
1911   'postcode': '30643'   'country': 'US'}}
1912   'postcode': '97220'   'country': 'US'}}
1913   'postcode': '67208'   'country': 'US'}}

[1914 rows x 2 columns]

In [27]:
zip_cntry_df['zip_only'] = zip_cntry_df['zip'].str.split(':', expand=True)[1]
zip_cntry_df['zip_only'].head()

/var/folders/92/3rr1k66j0p17gyjv6qwfhzr40000gn/T/ipykernel_87625/2892788863.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  zip_cntry_df['zip_only'] = zip_cntry_df['zip'].str.split(':', expand=True)[1]


0     '97071'
1     '63129'
2     '48021'
3     '38824'
4     '87107'
Name: zip_only, dtype: object

In [28]:
zip_cntry_df['cntry_only'] = zip_cntry_df['cntry'].str.split(':', expand=True)[1]
zip_cntry_df['cntry_only'].head()

/var/folders/92/3rr1k66j0p17gyjv6qwfhzr40000gn/T/ipykernel_87625/3074975475.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  zip_cntry_df['cntry_only'] = zip_cntry_df['cntry'].str.split(':', expand=True)[1]


0     'US'}}
1     'US'}}
2     'US'}}
3     'US'}}
4     'US'}}
Name: cntry_only, dtype: object

In [29]:
zip_cntry_df

zip               cntry  zip_only cntry_only
0      'postcode': '97071'   'country': 'US'}}   '97071'     'US'}}
1      'postcode': '63129'   'country': 'US'}}   '63129'     'US'}}
2      'postcode': '48021'   'country': 'US'}}   '48021'     'US'}}
3      'postcode': '38824'   'country': 'US'}}   '38824'     'US'}}
4      'postcode': '87107'   'country': 'US'}}   '87107'     'US'}}
...                    ...                 ...       ...        ...
1909   'postcode': '95035'   'country': 'US'}}   '95035'     'US'}}
1910   'postcode': '95035'   'country': 'US'}}   '95035'     'US'}}
1911   'postcode': '30643'   'country': 'US'}}   '30643'     'US'}}
1912   'postcode': '97220'   'country': 'US'}}   '97220'     'US'}}
1913   'postcode': '67208'   'country': 'US'}}   '67208'     'US'}}

[1914 rows x 4 columns]

In [30]:
zip_cntry_df = zip_cntry_df.drop(['zip', 'cntry'], axis=1)
print(zip_cntry_df)

      zip_only cntry_only
0      '97071'     'US'}}
1      '63129'     'US'}}
2      '48021'     'US'}}
3      '38824'     'US'}}
4      '87107'     'US'}}
...        ...        ...
1909   '95035'     'US'}}
1910   '95035'     'US'}}
1911   '30643'     'US'}}
1912   '97220'     'US'}}
1913   '67208'     'US'}}

[1914 rows x 2 columns]


In [31]:
zip_cntry_df= zip_cntry_df.rename(columns={'zip_only':'zip code','cntry_only':'country'})
zip_cntry_df.head()

zip code  country
0   '97071'   'US'}}
1   '63129'   'US'}}
2   '48021'   'US'}}
3   '38824'   'US'}}
4   '87107'   'US'}}

In [32]:
#pulling in just city and state columns 
zipcode_only_df= zip_cntry_df[['zip code']]
zipcode_only_df

zip code
0      '97071'
1      '63129'
2      '48021'
3      '38824'
4      '87107'
...        ...
1909   '95035'
1910   '95035'
1911   '30643'
1912   '97220'
1913   '67208'

[1914 rows x 1 columns]

In [33]:
zipcode_only_df['zip code'] = zipcode_only_df['zip code'].str.replace("'", "")

print(zipcode_only_df)

     zip code
0       97071
1       63129
2       48021
3       38824
4       87107
...       ...
1909    95035
1910    95035
1911    30643
1912    97220
1913    67208

[1914 rows x 1 columns]


/var/folders/92/3rr1k66j0p17gyjv6qwfhzr40000gn/T/ipykernel_87625/658138451.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  zipcode_only_df['zip code'] = zipcode_only_df['zip code'].str.replace("'", "")


In [34]:
country_only_df= zip_cntry_df[['country']]
country_only_df

country
0      'US'}}
1      'US'}}
2      'US'}}
3      'US'}}
4      'US'}}
...       ...
1909   'US'}}
1910   'US'}}
1911   'US'}}
1912   'US'}}
1913   'US'}}

[1914 rows x 1 columns]

In [39]:
country_only_df['country'] = country_only_df['country'].str.replace("'", "")

print(country_only_df)

     country
0       US}}
1       US}}
2       US}}
3       US}}
4       US}}
...      ...
1909    US}}
1910    US}}
1911    US}}
1912    US}}
1913    US}}

[1914 rows x 1 columns]


In [40]:
country_only_df['country'] = country_only_df['country'].str.replace('}', '', regex=True)
print(country_only_df)

     country
0         US
1         US
2         US
3         US
4         US
...      ...
1909      US
1910      US
1911      US
1912      US
1913      US

[1914 rows x 1 columns]


In [41]:
final_zip_country_df= pd.concat([zipcode_only_df, country_only_df], axis=1)

print(final_zip_country_df)

     zip code country
0       97071      US
1       63129      US
2       48021      US
3       38824      US
4       87107      US
...       ...     ...
1909    95035      US
1910    95035      US
1911    30643      US
1912    97220      US
1913    67208      US

[1914 rows x 2 columns]


In [42]:
final_location_df= pd.concat([final_city_state_df, final_zip_country_df], axis=1)

print(final_location_df)

              city state zip code country
0         Woodburn    OR    97071      US
1        St. Louis    MO    63129      US
2       Eastpointe    MI    48021      US
3          Baldwyn    MS    38824      US
4      Albuquerque    NM    87107      US
...            ...   ...      ...     ...
1909      Milpitas    CA    95035      US
1910      Milpitas    CA    95035      US
1911      Hartwell    GA    30643      US
1912      Portland    OR    97220      US
1913       Wichita    KS    67208      US

[1914 rows x 4 columns]


In [45]:
final_data_sheet_df= pd.concat([dropped_dup_df, final_location_df], axis=1)

print(final_data_sheet_df)

      Unnamed: 0          id organization_id                 name type    age  \
0            0.0  70490327.0          TX2305                Davon  Dog  Adult   
1            1.0  70490328.0           MO486                 Mack  Dog  Adult   
2            2.0  70490326.0           MI812  Lahni! DNA tested!   Dog  Adult   
3            3.0  70490283.0           MS214        Jughead Jones  Dog   Baby   
4            4.0  70490324.0            AZ57                 Mona  Dog  Young   
...          ...         ...             ...                  ...  ...    ...   
1895         NaN         NaN             NaN                  NaN  NaN    NaN   
1896         NaN         NaN             NaN                  NaN  NaN    NaN   
1899         NaN         NaN             NaN                  NaN  NaN    NaN   
1905         NaN         NaN             NaN                  NaN  NaN    NaN   
1907         NaN         NaN             NaN                  NaN  NaN    NaN   

      gender         size  

In [46]:
final_data_sheet_df

Unnamed: 0          id organization_id                 name type    age  \
0            0.0  70490327.0          TX2305                Davon  Dog  Adult   
1            1.0  70490328.0           MO486                 Mack  Dog  Adult   
2            2.0  70490326.0           MI812  Lahni! DNA tested!   Dog  Adult   
3            3.0  70490283.0           MS214        Jughead Jones  Dog   Baby   
4            4.0  70490324.0            AZ57                 Mona  Dog  Young   
...          ...         ...             ...                  ...  ...    ...   
1895         NaN         NaN             NaN                  NaN  NaN    NaN   
1896         NaN         NaN             NaN                  NaN  NaN    NaN   
1899         NaN         NaN             NaN                  NaN  NaN    NaN   
1905         NaN         NaN             NaN                  NaN  NaN    NaN   
1907         NaN         NaN             NaN                  NaN  NaN    NaN   

      gender         size  \
0       Male        Large   
1     Female  Extra Large   
2     Female        Large   
3       Male        Large   
4     Female        Large   
...      ...          ...   
1895     NaN          NaN   
1896     NaN          NaN   
1899     NaN          NaN   
1905     NaN          NaN   
1907     NaN          NaN   

                                                                                                                                                                                            contact  \
0                   {'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}   
1                {'email': 'wonderweimsrescue@gmail.com', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'St. Louis', 'state': 'MO', 'postcode': '63129', 'country': 'US'}}   
2        {'email': 'misfitangels@gmail.com', 'phone': '(586) 339-5443', 'address': {'address1': None, 'address2': None, 'city': 'Eastpointe', 'state': 'MI', 'postcode': '48021', 'country': 'US'}}   
3           {'email': 'myjerichorfb@gmail.com', 'phone': '(662) 401-5799', 'address': {'address1': None, 'address2': None, 'city': 'Baldwyn', 'state': 'MS', 'postcode': '38824', 'country': 'US'}}   
4     {'email': 'blackhathumane@gmail.com', 'phone': '(575) 999-6236', 'address': {'address1': None, 'address2': None, 'city': 'Albuquerque', 'state': 'NM', 'postcode': '87107', 'country': 'US'}}   
...                                                                                                                                                                                             ...   
1895                                                                                                                                                                                            NaN   
1896                                                                                                                                                                                            NaN   
1899                                                                                                                                                                                            NaN   
1905                                                                                                                                                                                            NaN   
1907                                                                                                                                                                                            NaN   

                                                                                                                                                                                                          url  \
0     https://www.petfinder.com/dog/davon-70490327/or/woodburn/throw-a-dog-a-bone-dog-

In [47]:
completed_data_df = final_data_sheet_df.dropna()
completed_data_df.count()

Unnamed: 0         1624
id                 1624
organization_id    1624
name               1624
type               1624
age                1624
gender             1624
size               1624
contact            1624
url                1624
city               1624
state              1624
zip code           1624
country            1624
dtype: int64

In [48]:
completed_data_df

Unnamed: 0          id organization_id                 name type    age  \
0            0.0  70490327.0          TX2305                Davon  Dog  Adult   
1            1.0  70490328.0           MO486                 Mack  Dog  Adult   
2            2.0  70490326.0           MI812  Lahni! DNA tested!   Dog  Adult   
3            3.0  70490283.0           MS214        Jughead Jones  Dog   Baby   
4            4.0  70490324.0            AZ57                 Mona  Dog  Young   
...          ...         ...             ...                  ...  ...    ...   
1909      1954.0  70487515.0           TX236                DOBBY  Dog   Baby   
1910      1955.0  70487520.0           TX236                 ROXY  Dog  Young   
1911      1956.0  70487517.0           TX236                ROCKO  Dog  Adult   
1912      1957.0  70487514.0           TX236             A1201906  Dog  Young   
1913      1958.0  70487518.0           TX236               DIPSEY  Cat   Baby   

      gender         size  \
0       Male        Large   
1     Female  Extra Large   
2     Female        Large   
3       Male        Large   
4     Female        Large   
...      ...          ...   
1909    Male       Medium   
1910  Female        Large   
1911    Male        Large   
1912    Male        Small   
1913    Male        Large   

                                                                                                                                                                                                    contact  \
0                           {'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}   
1                        {'email': 'wonderweimsrescue@gmail.com', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'St. Louis', 'state': 'MO', 'postcode': '63129', 'country': 'US'}}   
2                {'email': 'misfitangels@gmail.com', 'phone': '(586) 339-5443', 'address': {'address1': None, 'address2': None, 'city': 'Eastpointe', 'state': 'MI', 'postcode': '48021', 'country': 'US'}}   
3                   {'email': 'myjerichorfb@gmail.com', 'phone': '(662) 401-5799', 'address': {'address1': None, 'address2': None, 'city': 'Baldwyn', 'state': 'MS', 'postcode': '38824', 'country': 'US'}}   
4             {'email': 'blackhathumane@gmail.com', 'phone': '(575) 999-6236', 'address': {'address1': None, 'address2': None, 'city': 'Albuquerque', 'state': 'NM', 'postcode': '87107', 'country': 'US'}}   
...                                                                                                                                                                                                     ...   
1909  {'email': 'dasadopt@dallas.gov', 'phone': '(214) 671-0249', 'address': {'address1': '1818 N. Westmoreland', 'address2': None, 'city': 'Dallas', 'state': 'TX', 'postcode': '75212', 'country': 'US'}}   
1910  {'email': 'dasadopt@dallas.gov', 'phone': '(214) 671-0249', 'address': {'address1': '1818 N. Westmoreland', 'address2': None, 'city': 'Dallas', 'state': 'TX', 'postcode': '75212', 'country': 'US'}}   
1911  {'email': 'dasadopt@dallas.gov', 'phone': '(214) 671-0249', 'address': {'address1': '1818 N. Westmoreland', 'address2': None, 'city': 'Dallas', 'state': 'TX', 'postcode': '75212', 'country': 'US'}}   
1912  {'email': 'dasadopt@dallas.gov', 'phone': '(214) 671-0249', 'address': {'address1': '1818 N. Westmoreland', 'address2': None, 'city': 'Dallas', 'state': 'TX', 'postcode': '75212', 'country': 'US'}}   
1913  {'email': 'dasadopt@dallas.gov', 'phone': '(214) 671-0249', 'address': {'address1': '1818 N. Westmoreland', 'address2': None, 'city': 'Dallas', 'state': 'TX', 'postcode': '75212', 'country': 'US'}}   

                                                                                                                                                                                                       

In [49]:
completed_data_df = completed_data_df.drop(['contact'], axis=1)
print(completed_data_df)

      Unnamed: 0          id organization_id                 name type    age  \
0            0.0  70490327.0          TX2305                Davon  Dog  Adult   
1            1.0  70490328.0           MO486                 Mack  Dog  Adult   
2            2.0  70490326.0           MI812  Lahni! DNA tested!   Dog  Adult   
3            3.0  70490283.0           MS214        Jughead Jones  Dog   Baby   
4            4.0  70490324.0            AZ57                 Mona  Dog  Young   
...          ...         ...             ...                  ...  ...    ...   
1909      1954.0  70487515.0           TX236                DOBBY  Dog   Baby   
1910      1955.0  70487520.0           TX236                 ROXY  Dog  Young   
1911      1956.0  70487517.0           TX236                ROCKO  Dog  Adult   
1912      1957.0  70487514.0           TX236             A1201906  Dog  Young   
1913      1958.0  70487518.0           TX236               DIPSEY  Cat   Baby   

      gender         size  

In [50]:
completed_data_df

Unnamed: 0          id organization_id                 name type    age  \
0            0.0  70490327.0          TX2305                Davon  Dog  Adult   
1            1.0  70490328.0           MO486                 Mack  Dog  Adult   
2            2.0  70490326.0           MI812  Lahni! DNA tested!   Dog  Adult   
3            3.0  70490283.0           MS214        Jughead Jones  Dog   Baby   
4            4.0  70490324.0            AZ57                 Mona  Dog  Young   
...          ...         ...             ...                  ...  ...    ...   
1909      1954.0  70487515.0           TX236                DOBBY  Dog   Baby   
1910      1955.0  70487520.0           TX236                 ROXY  Dog  Young   
1911      1956.0  70487517.0           TX236                ROCKO  Dog  Adult   
1912      1957.0  70487514.0           TX236             A1201906  Dog  Young   
1913      1958.0  70487518.0           TX236               DIPSEY  Cat   Baby   

      gender         size  \
0       Male        Large   
1     Female  Extra Large   
2     Female        Large   
3       Male        Large   
4     Female        Large   
...      ...          ...   
1909    Male       Medium   
1910  Female        Large   
1911    Male        Large   
1912    Male        Small   
1913    Male        Large   

                                                                                                                                                                                                          url  \
0     https://www.petfinder.com/dog/davon-70490327/or/woodburn/throw-a-dog-a-bone-dog-rescue-tx2305/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7c...   
1     https://www.petfinder.com/dog/mack-70490328/mo/st-louis/wonder-weims-rescue-mo486/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7ce2fffe-d69d-...   
2     https://www.petfinder.com/dog/lahni-dna-tested-70490326/mi/eastpointe/misfit-angels-dog-rescue-mi812/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_con...   
3     https://www.petfinder.com/dog/jughead-jones-70490283/ms/baldwyn/jericho-rescued-fur-babies-ms214/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content...   
4     https://www.petfinder.com/dog/mona-70490324/nm/albuquerque/blackhat-humane-society-az57/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7ce2fffe...   
...                                                                                                                                                                                                       ...   
1909  https://www.petfinder.com/dog/dobby-70487515/tx/dallas/dallas-animal-services-and-adoption-center-tx236/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_...   
1910  https://www.petfinder.com/dog/roxy-70487520/tx/dallas/dallas-animal-services-and-adoption-center-tx236/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_c...   
1911  https://www.petfinder.com/dog/rocko-70487517/tx/dallas/dallas-animal-services-and-adoption-center-tx236/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_...   
1912  https://www.petfinder.com/dog/a1201906-70487514/tx/dallas/dallas-animal-services-and-adoption-center-tx236/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&u...   
1913  https://www.petfinder.com/cat/dipsey-70487518/tx/dallas/dallas-animal-services-and-adoption-center-tx236/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm...   

              city state zip code country  
0         Woodburn    OR    97071      US  
1        St. Louis    MO    63129      US  
2       Eastpointe    MI    48021      US  

In [51]:
completed_data_df.to_csv('completed_clean_data.csv')

In [22]:
location_df= pd.DataFrame(final_city_state_df)

location_df['location'] = location_df['city'] + ' ' + location_df['state']

print(location_df)

                city  state              location
0         'Woodburn'   'OR'      'Woodburn'  'OR'
1        'St. Louis'   'MO'     'St. Louis'  'MO'
2       'Eastpointe'   'MI'    'Eastpointe'  'MI'
3          'Baldwyn'   'MS'       'Baldwyn'  'MS'
4      'Albuquerque'   'NM'   'Albuquerque'  'NM'
...              ...    ...                   ...
1909      'Milpitas'   'CA'      'Milpitas'  'CA'
1910      'Milpitas'   'CA'      'Milpitas'  'CA'
1911      'Hartwell'   'GA'      'Hartwell'  'GA'
1912      'Portland'   'OR'      'Portland'  'OR'
1913       'Wichita'   'KS'       'Wichita'  'KS'

[1914 rows x 3 columns]


In [23]:
location_df = location_df.drop(['city', 'state'], axis=1)
print(location_df)

                  location
0         'Woodburn'  'OR'
1        'St. Louis'  'MO'
2       'Eastpointe'  'MI'
3          'Baldwyn'  'MS'
4      'Albuquerque'  'NM'
...                    ...
1909      'Milpitas'  'CA'
1910      'Milpitas'  'CA'
1911      'Hartwell'  'GA'
1912      'Portland'  'OR'
1913       'Wichita'  'KS'

[1914 rows x 1 columns]


In [24]:
location_df['location'] = location_df['location'].str.replace("'", "")

print(location_df)

              location
0         Woodburn  OR
1        St. Louis  MO
2       Eastpointe  MI
3          Baldwyn  MS
4      Albuquerque  NM
...                ...
1909      Milpitas  CA
1910      Milpitas  CA
1911      Hartwell  GA
1912      Portland  OR
1913       Wichita  KS

[1914 rows x 1 columns]


In [25]:
location_df

location
0         Woodburn  OR
1        St. Louis  MO
2       Eastpointe  MI
3          Baldwyn  MS
4      Albuquerque  NM
...                ...
1909      Milpitas  CA
1910      Milpitas  CA
1911      Hartwell  GA
1912      Portland  OR
1913       Wichita  KS

[1914 rows x 1 columns]

In [26]:
location_df

location
0         Woodburn  OR
1        St. Louis  MO
2       Eastpointe  MI
3          Baldwyn  MS
4      Albuquerque  NM
...                ...
1909      Milpitas  CA
1910      Milpitas  CA
1911      Hartwell  GA
1912      Portland  OR
1913       Wichita  KS

[1914 rows x 1 columns]

In [ ]:
### End of Kyle's Code ###

In [151]:
#load data into a list then load list as dataframe 
values_to_list= dropped_dup_df['contact'].values.tolist()
address_data_df= pd.DataFrame(values_to_list)
address_data_df.head()

0
0                {'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}
1             {'email': 'wonderweimsrescue@gmail.com', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'St. Louis', 'state': 'MO', 'postcode': '63129', 'country': 'US'}}
2     {'email': 'misfitangels@gmail.com', 'phone': '(586) 339-5443', 'address': {'address1': None, 'address2': None, 'city': 'Eastpointe', 'state': 'MI', 'postcode': '48021', 'country': 'US'}}
3        {'email': 'myjerichorfb@gmail.com', 'phone': '(662) 401-5799', 'address': {'address1': None, 'address2': None, 'city': 'Baldwyn', 'state': 'MS', 'postcode': '38824', 'country': 'US'}}
4  {'email': 'blackhathumane@gmail.com', 'phone': '(575) 999-6236', 'address': {'address1': None, 'address2': None, 'city': 'Albuquerque', 'state': 'NM', 'postcode': '87107', 'country': 'US'}}

In [169]:
# Take a look at the data. 
address_data_df[0]

0                       {'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}
1                    {'email': 'wonderweimsrescue@gmail.com', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'St. Louis', 'state': 'MO', 'postcode': '63129', 'country': 'US'}}
2            {'email': 'misfitangels@gmail.com', 'phone': '(586) 339-5443', 'address': {'address1': None, 'address2': None, 'city': 'Eastpointe', 'state': 'MI', 'postcode': '48021', 'country': 'US'}}
3               {'email': 'myjerichorfb@gmail.com', 'phone': '(662) 401-5799', 'address': {'address1': None, 'address2': None, 'city': 'Baldwyn', 'state': 'MS', 'postcode': '38824', 'country': 'US'}}
4         {'email': 'blackhathumane@gmail.com', 'phone': '(575) 999-6236', 'address': {'address1': None, 'address2': None, 'city': 'Albuquerque', 'state': 'NM', 'postcode': '87107', 'country': 'US'}}


In [170]:
# Get the column names and data types. 
address_data_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1914 entries, 0 to 1913
Data columns (total 1 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   0       1914 non-null   object
dtypes: object(1)
memory usage: 15.1+ KB


In [172]:
first_row_data = address_data_df.iloc[0][0]
first_row_data

"{'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}"

In [181]:
type(first_row_data)

str

In [182]:
first_row = eval(first_row_data)
type(first_row)

dict

In [185]:
# Assuming first_row_data is a JSON-like string with single quotes around keys
first_row_data = address_data_df.iloc[0][0]

# Evaluate the string as a Python literal to convert it to a dictionary
first_row = eval(first_row_data)

# Print the type and content of first_row
# print("Type of first_row:", type(first_row))
# print("Content of first_row:")
for k, v in first_row.items():
    print(k)
    print(v)

email
rescue@throwadogabone.org
phone
None
address
{'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}


In [188]:
# 1. Create two list one for the keys and one for the values.
values = []
column_names = []
#  2. Iterate through the DataFrame.
for i, row in address_data_df.iterrows():
    data = row[0]
   # Use a list comprehension to get the keys from the converted data.
    columns = [k for k,v in address_data_df.items()]
    # Use a list comprehension to get the values for each row.
    row_values = [v for k, v in address_data_df.items()]
    # Append the keys and list values to the lists created in step 1.  
    column_names.append(columns)
    values.append(row_values)

# Print out the keys and list of values for each row.
print(column_names)
print(values)

[[0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0], [0],

In [ ]:
# The default port used by MongoDB is 27017
# https://docs.mongodb.com/manual/reference/default-mongodb-port/
mongo = MongoClient(port=27017)

# Define the 'classDB' database in Mongo
db = mongo.project_3

In [57]:
#look for collections 
db.list_collection_names()
#pull first entry to confirm correct collection was pulled
db.cleaned_animals.find_one()

{'_id': ObjectId('65b20704e97a089c2909687e'),
 'Unnamed: 0': 0,
 'id': 70490327,
 'organization_id': 'TX2305',
 'name': 'Davon',
 'type': 'Dog',
 'age': 'Adult',
 'gender': 'Male',
 'size': 'Large',
 'contact': "{'email': 'rescue@throwadogabone.org', 'phone': None, 'address': {'address1': None, 'address2': None, 'city': 'Woodburn', 'state': 'OR', 'postcode': '97071', 'country': 'US'}}",
 'url': 'https://www.petfinder.com/dog/davon-70490327/or/woodburn/throw-a-dog-a-bone-dog-rescue-tx2305/?referrer_id=7ce2fffe-d69d-41b9-a989-d0e245bd21fd&utm_source=api&utm_medium=partnership&utm_content=7ce2fffe-d69d-41b9-a989-d0e245bd21fd'}